# A story of failures in the optimisation of Water Distribution Systems.

Aware of the computational needs of our idea (joint optimisation of WDS design and operation), I started the development of a C++ Library to work as an interface between an optimization library and a hydraulic simulation library.



In [1]:
# Imports
import os
import sys
import plotly.express as px
import plotly.graph_objects as go
import plotly.subplots as subp
import pandas as pd
import numpy as np

import pygmo as pg

sys.path.append('..')
import pybeme

In [2]:
# Load the experiments, prepare the plots
experiments = pybeme.load_experiments(os.path.join('data', 'all'), verbose=False)

In [3]:
# Plot the pareto front of the first round of experiments.
# There is something wrong, so plot the Head and pressure for the tanks, junctions
msize = 10
xlims = [-.5e6, 20.5e6]
ylims = [-0.05, 0.605]
xaxis_title_text='Cost [$]'
yaxis_title_text='OF Reliability Index f1 [-]'
title_font_size=20
legend_font_size=16
def_font_size=12
def fix_layout(a_fig: go.Figure, a_title: str) -> None:
    a_fig.update_layout(title=dict(
                            text=a_title,
                            xanchor='center',
                            x=0.5,
                            yanchor='top',
                            y=1,
                            font_size=title_font_size
                        ),
                        plot_bgcolor='white',
                        paper_bgcolor='white',
                        xaxis=dict(
                            title=xaxis_title_text,
                            range=xlims,
                            automargin=True,
                            showline=True,
                            showgrid=True,
                            linewidth=1,
                            linecolor='grey',
                            zerolinecolor='black',
                            gridcolor='lightgrey'
                        ),
                        yaxis=dict(
                            title=yaxis_title_text,
                            range=ylims,
                            automargin=True,
                            showline=True,
                            showgrid=True,
                            linewidth=1,
                            linecolor='grey',
                            zerolinecolor='black',
                            gridcolor='lightgrey'
                        ),
                        width=1200,
                        height=800,
                        font=dict(
                            family="Lato",
                            color="black",
                            size=def_font_size
                        ),
                        margin=dict(
                            l=10,
                            r=10,
                            b=10,
                            t=50,
                            pad=0
                        ),
                        showlegend=True,
                        legend=dict(
                            orientation="v",
                            xanchor="left",
                            x=0.03,  
                            yanchor="top",
                            y=0.9,  
                            itemsizing='trace',  # To ensure items in legend keep the same size
                            traceorder="normal",
                            bgcolor="White",  # Background color
                            bordercolor="Black",  # Border color
                            borderwidth=1,  # Border width
                            groupclick="toggleitem",
                            itemclick="toggleothers",
                            itemdoubleclick="toggle",
                            tracegroupgap=100,
                            font_size=legend_font_size
                        )
)

def filter_pf(experiment: pybeme.Experiment):
    final_fvs = experiment.final_fitness_vectors.to_numpy()
    pf = pg.non_dominated_front_2d(final_fvs)
    pf = pf[final_fvs[pf,0] < 20e6]
    pf = pf[final_fvs[pf,1] < 0]
    return pf

def plot_pareto_fronts(experiments: dict, exps2plot: list, colors: list, markers: list, names: list):
    fig = go.Figure()

    for e, expname, in enumerate(exps2plot):
        final_fvs = experiments[expname].final_fitness_vectors.to_numpy()
        pf = filter_pf(experiments[expname])
        npf = np.setdiff1d(np.arange(final_fvs.shape[0]), pf)
        
        fig.add_trace(go.Scatter(x=final_fvs[pf,0], y=-final_fvs[pf,1], mode='markers',
                                marker=dict(size=msize, symbol=markers[e], color=colors[e]),  
                                showlegend=True, name=names[e],
                                legendgroup=expname,
                                customdata=np.array(pf, dtype=str),
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f} <extra>%{customdata}</extra>'
                                ) )
        fig.add_trace(go.Scatter(x=final_fvs[npf,0], y=-final_fvs[npf,1], mode='markers', opacity=0.5,
                                marker=dict(size=msize, symbol=markers[e]+'-open', color=colors[e]),  
                                showlegend=True, name=names[e],
                                legendgroup=expname,
                                customdata=np.array(npf, dtype=str),
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f} <extra>%{customdata}</extra>'
                                ) )

    fix_layout(fig, 'Pareto fronts of the different solutions')

    fig.show()

def percentage_errors(pre, post):
    pe = (pre - post) / np.abs(pre)
    # Failed solution have rel indx >= 0
    pe[post[:,1] >= 0, :] = -0.99
    return pe

def version_title_matrix(vers2test: list) -> list:
    assert len(vers2test) == 2, 'Only two versions are supported'
    titles = ["", f"{vers2test[0]} -> {vers2test[1]}", "", f"{vers2test[1]} -> {vers2test[0]}", "", "", "", ""]
    return titles

def plot_version_mismatch():
    fig = subp.make_subplots(rows=2, cols=4, subplot_titles=version_title_matrix(versions2test),
                            shared_xaxes=True, shared_yaxes=True,
                            vertical_spacing=0.01, horizontal_spacing=0.01,
                            row_heights=[0.8, 0.2], column_widths=[0.1, 0.4, 0.1, 0.4],
                            x_title="Evaluation version")
    fig.update_layout(width=1200, height=600)
    for c in range(1,5):
        for r in range(1, 3):
            fig.update_xaxes(showline=True, showgrid=True, linewidth=1, linecolor='grey', zerolinecolor='black', gridcolor='lightgrey', mirror=True,
                             range=[-1.01, 1.01],
                             row=r, col=c)
            fig.update_yaxes(showline=True, showgrid=True, linewidth=1, linecolor='grey', zerolinecolor='black', gridcolor='lightgrey', mirror=True,
                              range=[-1.01, 1.01],
                              row=r, col=c)
            fig.update_layout(plot_bgcolor='white', paper_bgcolor='white') 
    fig.update_xaxes(title_text='Cost percentage error', row=2, col=2)
    fig.update_xaxes(title_text='Cost percentage error', row=2, col=4)
    fig.update_yaxes(title_text='RelIdx percentage error', row=1, col=1)

    for e, expname in enumerate(exps2plot):
        final_fvs = experiments[expname].final_fitness_vectors
        pf_idx = filter_pf(experiments[expname])
        pf_pre = final_fvs.to_numpy()[pf_idx]
        final_indvs_coords = final_fvs.index[pf_idx]

        pf_post = np.zeros_like(pf_pre)
        for i, fic in enumerate(final_indvs_coords):
            final_indv_coord = (fic[0], # island name
                                experiments[expname].generations[fic[0]].to_numpy()[-1], # last generation of the island
                                fic[1]) # individual index

            sim = experiments[expname].simulator(final_indv_coord)
            
            if e % 2 == 0:
                valt = versions2test[1]
                valt_column = 2
            else:
                valt = versions2test[0]
                valt_column = 4
            
            sim.data['bemelib_version'] = valt
            sim.run()
            pf_post[i] = sim.result

        pe = percentage_errors(pf_pre, pf_post)
        pe_sux = pe[pe[:,1] != -0.99, :]
        fig.add_trace(go.Scatter(x=pe_sux[:,0], y=pe_sux[:,1], mode='markers',
                                marker=dict(size=msize, symbol=markers[e], color=colors[e]),
                                showlegend=False,
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f}'
                                ), row=1, col=valt_column)
        pe_fail = pe[pe[:,1] == -0.99, :]
        fig.add_trace(go.Scatter(x=pe_fail[:,0], y=pe_fail[:,1], mode='markers',
                                marker=dict(size=msize, symbol=markers[e], color=colors[e], line=dict(color='red', width=1)),  
                                showlegend=False,
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f}'
                                ), row=1, col=valt_column)
        
        # Add the distribution of the cost error, in the same column, but second row
        deltac_counts, deltac_bins = np.histogram(pe[:,0], bins=np.linspace(-1, 1, 20))
        fig.add_trace(go.Bar(x=deltac_bins+((deltac_bins[1]-deltac_bins[0])/2), y=deltac_counts/np.sum(deltac_counts), width=(deltac_bins[1]-deltac_bins[0]),
                            opacity=0.75,
                            marker=dict(color=colors[e]), showlegend=False), row=2, col=valt_column)

        # Add the distribution of the reliability index error, in the first row, but one column before
        deltar_counts, deltar_bins = np.histogram(pe[:,1], bins=np.linspace(-1, 1, 20))
        fig.add_trace(go.Bar(y=deltar_bins+((deltar_bins[1]-deltar_bins[0])/2), x=deltar_counts/np.sum(deltar_counts), width=(deltar_bins[1]-deltar_bins[0]), orientation='h',
                            opacity=0.75,
                            marker=dict(color=colors[e]), showlegend=False), row=1, col=valt_column-1)

        # Add the centroid of the error distribution
        fig.add_trace(go.Scatter(x=[np.mean(pe[:,0])], y=[np.mean(pe[:,1])], mode='markers',
                                marker=dict(size=2*msize, symbol='x-open', color=colors[e], line=dict(color=colors[e], width=1)),  
                                showlegend=False,
                                customdata=[np.mean(pe[:,0]), np.mean(pe[:,1])],
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f} <extra>%{customdata}</extra>'
                                ), row=1, col=valt_column)
    
    fig.update_layout(barmode='overlay')
    fig.show()

def plot_formulation_mismatch():
    fig = subp.make_subplots(rows=2, cols=4, subplot_titles=version_title_matrix(formulations2test),
                            shared_xaxes=True, shared_yaxes=True,
                            vertical_spacing=0.01, horizontal_spacing=0.01,
                            row_heights=[0.8, 0.2], column_widths=[0.1, 0.4, 0.1, 0.4],
                            x_title="Evaluation Formulation")
    fig.update_layout(width=1200, height=600)
    for c in range(1,5):
        for r in range(1, 3):
            fig.update_xaxes(showline=True, showgrid=True, linewidth=1, linecolor='grey', zerolinecolor='black', gridcolor='lightgrey', mirror=True,
                             range=[-1.01, 1.01],
                             row=r, col=c)
            fig.update_yaxes(showline=True, showgrid=True, linewidth=1, linecolor='grey', zerolinecolor='black', gridcolor='lightgrey', mirror=True,
                              range=[-1.01, 1.01],
                              row=r, col=c)
            fig.update_layout(plot_bgcolor='white', paper_bgcolor='white') 
    fig.update_xaxes(title_text='Cost percentage error', row=2, col=2)
    fig.update_xaxes(title_text='Cost percentage error', row=2, col=4)
    fig.update_yaxes(title_text='RelIdx percentage error', row=1, col=1)

    for e, expname in enumerate(exps2plot):
        final_fvs = experiments[expname].final_fitness_vectors
        pf_idx = filter_pf(experiments[expname])
        pf_pre = final_fvs.to_numpy()[pf_idx]
        final_indvs_coords = final_fvs.index[pf_idx]

        pf_post = np.zeros_like(pf_pre)
        for i, fic in enumerate(final_indvs_coords):
            final_indv_coord = (fic[0], # island name
                                experiments[expname].generations[fic[0]].to_numpy()[-1], # last generation of the island
                                fic[1]) # individual index

            sim = experiments[expname].simulator(final_indv_coord)

            # Convert from one formulation to another:
            if e % 2 == 0:
                sim.convert_to_formulation(formulations2test[1])
                valt_column = 2
            else:
                sim.convert_to_formulation(formulations2test[0])
                valt_column = 4
            
            sim.run()
            pf_post[i] = sim.result

        pe = percentage_errors(pf_pre, pf_post)
        pe_sux = pe[pe[:,1] != -0.99, :]
        fig.add_trace(go.Scatter(x=pe_sux[:,0], y=pe_sux[:,1], mode='markers',
                                marker=dict(size=msize, symbol=markers[e], color=colors[e]),
                                showlegend=False,
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f}'
                                ), row=1, col=valt_column)
        pe_fail = pe[pe[:,1] == -0.99, :]
        fig.add_trace(go.Scatter(x=pe_fail[:,0], y=pe_fail[:,1], mode='markers',
                                marker=dict(size=msize, symbol=markers[e], color=colors[e], line=dict(color='red', width=1)),  
                                showlegend=False,
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f}'
                                ), row=1, col=valt_column)
        
        # Add the distribution of the cost error, in the same column, but second row
        deltac_counts, deltac_bins = np.histogram(pe[:,0], bins=np.linspace(-1, 1, 20))
        fig.add_trace(go.Bar(x=deltac_bins+((deltac_bins[1]-deltac_bins[0])/2), y=deltac_counts/np.sum(deltac_counts), width=(deltac_bins[1]-deltac_bins[0]),
                            opacity=0.75,
                            marker=dict(color=colors[e]), showlegend=False), row=2, col=valt_column)

        # Add the distribution of the reliability index error, in the first row, but one column before
        deltar_counts, deltar_bins = np.histogram(pe[:,1], bins=np.linspace(-1, 1, 20))
        fig.add_trace(go.Bar(y=deltar_bins+((deltar_bins[1]-deltar_bins[0])/2), x=deltar_counts/np.sum(deltar_counts), width=(deltar_bins[1]-deltar_bins[0]), orientation='h',
                            opacity=0.75,
                            marker=dict(color=colors[e]), showlegend=False), row=1, col=valt_column-1)

        # Add the centroid of the error distribution
        fig.add_trace(go.Scatter(x=[np.mean(pe[:,0])], y=[np.mean(pe[:,1])], mode='markers',
                                marker=dict(size=2*msize, symbol='x-open', color=colors[e], line=dict(color=colors[e], width=1)),  
                                showlegend=False,
                                customdata=[np.mean(pe[:,0]), np.mean(pe[:,1])],
                                hovertemplate='Cost: %{x:2.2f} <br> Reliability Index: %{y:.2f} <extra>%{customdata}</extra>'
                                ), row=1, col=valt_column)
    
    fig.update_layout(barmode='overlay')
    fig.show()

In [4]:
# exps2plot = ['nsga2__anytown_mixed_f1__exp02', 'nsga2__anytown_rehab_f1__exp04', 'nsga2__anytown_rehab_f1__fullpower', 'nsga2__anytown_rehab_f1__median']
exps2plot = ['005', '004', '007', '008']
colors = ['#29378A', '#808080', '#74BDA7','#02B9EA']
markers = ['circle', 'circle', 'square', 'diamond']
names = ['Integrated', 'Pure design - wrong - Siew et al.', 'Pure design - Full power', 'Pure design - Median pattern']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)

There is something wrong, we checked and I forgot to track the missing steps. This is not ok but it is the default behaviour with wntr...
with EPYT this is not hte the behaviour if u use getComputedHydraulicTimeSeries.

## v 24.06.0 aka Calculate Ir with all instants
We fixed the use of all the instances. now we have the correct reliability

In [5]:
exps2plot = ['005', '011', '009', '010']
colors = ['#29378A', '#29378A', '#808080', '#808080']
markers = ['circle', 'square', 'circle', 'square']
names = ['Integrated - v24.4.0', 'Integrated - v24.6.0', 'Pure design - v24.4.0', 'Pure design - v24.6.0']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)    

versions2test = ['v24.01.00', 'v24.06.00']
plot_version_mismatch()

Standard output:
  Page 1                                    Mon Mar 17 18:16:34 2025

  ******************************************************************
  *                           E P A N E T                          *
  *                   Hydraulic and Water Quality                  *
  *                   Analysis for Pipe Networks                   *
  *                         Version 2.3                            *
  ******************************************************************
  
Thanks for using BeMe-Sim!

Element with ID: 3199511697077875288 evaluated.
	Fitness vector: [5.742e+06, 4.33628e+06]
	Elapsed time: 0 ms
Results saved in: /Users/zannads/repos/BevarMejo/visual/3199511697077875288.fv.json
EPANET project deleted

Standard error:
An error happend while executing a post-run task:
Task: Check correctness
function: check_correctness
  where: /Users/zannads/repos/BevarMejo/cli/src/simulator.cpp, 488
  what: Simulations results don't match the expected fitness vect

Ok but still not happy so we decided to do shorter hydraulics because we were experimenting the same behavoiur 

In [6]:
exps2plot = ['011', '013', '015',
             '010', '012', '014']
colors = ['#29378A', '#29378A', '#29378A',
          '#808080', '#808080', '#808080']
markers = ['circle', 'square', 'diamond',
           'circle', 'square', 'diamond']
names = ['Integrated - 60min', 'Integrated - 30min', 'Integrated - 15min',
        'Pure design - 60min', 'Pure design - 30min', 'Pure design - 15min']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)



## Exisisting pipes formulation 1 (Farmani) vs formulation 2 (mine & Mark)

1. fexp1: [0: do nothing, 1 clean, 2 install] x [0->9: pipe rehabilitation alternative (active only if previous set to 2)]

2. fexp2: [0: do nothing, 1 clean, 2->11 pipe rehabilitation_alternative]

In [7]:
exps2plot = ['015', '017', '014', '016']
colors = ['#29378A', '#29378A', '#808080', '#808080']
markers = ['circle', 'square', 'circle', 'square']
names = ['Integrated - Existing Pipe F1', 'Integrated - Existing Pipe F2', 'Pure design - Existing Pipe F1', 'Pure design - Existing Pipe F2']
legendgroup_titles = ['Integrated', 'Integrated', 'Pure design', 'Pure design']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)

# Plot the HV to see if the f2 works better than f1. One HV value per each generation. Do it for each island
fig = go.Figure()
hv_refpoint = [0,0]
linestyles = ['solid', 'dashdot', 'solid', 'dashdot']
for e, expname in enumerate(exps2plot):
    genz = experiments[expname].generations
    fvs = experiments[expname].fitness_vectors
    # I will draw one line for each island
    for i, isl in enumerate(list(experiments[expname].data['archipelago']['islands'].keys())):
        n_reps = genz[isl].shape[0]
        hv = np.zeros(genz[isl].shape[0])
        for g, gen in enumerate(genz[isl]):
            datapoint = fvs.loc[isl].loc[gen].to_numpy()
            datapoint = datapoint[np.logical_and(datapoint[:,0]>0, datapoint[:,1]<0, datapoint[:,0] <= 20e6), :]
            if (datapoint.shape[0] > 0):
                datapoint[:,0] = -datapoint[:,0]/20e6
                hv[g] = pg.hypervolume(datapoint).compute(hv_refpoint)

        fig.add_trace(go.Scatter(x=genz[isl], y=hv, mode='lines',
                                marker=dict(size=msize, symbol=markers[e], color=colors[e]),
                                line=dict(width=2, dash=linestyles[e]),
                                showlegend=True, name=isl,
                                legendgroup=expname,
                                legendgrouptitle_text=names[e],
                                customdata=np.array(np.arange(genz[isl].shape[0]), dtype=str),
                                hovertemplate='Generation: %{x} <br> HV: %{y:.2f} <extra>%{customdata}</extra>'
                                ))

#fix_layout(fig, 'Hypervolume of the different solutions')
fig.update_layout(legend=dict(groupclick="toggleitem"))
fig.show()

# Plot the re-evaluation on the different formulations
formulations2test = [1, 2]
plot_formulation_mismatch()

Standard output:
  Page 1                                    Mon Mar 17 18:16:40 2025

  ******************************************************************
  *                           E P A N E T                          *
  *                   Hydraulic and Water Quality                  *
  *                   Analysis for Pipe Networks                   *
  *                         Version 2.3                            *
  ******************************************************************
  
Thanks for using BeMe-Sim!

Element with ID: 18095577331372847907 evaluated.
	Fitness vector: [6.59574e+06, -0.000156216]
	Elapsed time: 0 ms
Results saved in: /Users/zannads/repos/BevarMejo/visual/18095577331372847907.fv.json
EPANET project deleted

Standard error:

Return code:
0
Standard output:
  Page 1                                    Mon Mar 17 18:16:40 2025

  ******************************************************************
  *                           E P A N E T                

So we have a double benefit with this formulation:
1. in the integrated, more seeds converge.
2. in both, we don't really converge sooner, but we started from more feasible solutions...

## v24.11.0 aka BUG: check for invalid solutions in DDA

I was checking Head > 0 while I should have been checking Head > Elevation.
This bug should have no or little impact as the soultions with Head > 0 but < Elevetaion should be few.

In [8]:
# Same as before. We need to check v24.10.0 vs 24.11.0 for the mixed and rehab solutions
exps2plot = ['017', '019', '016', '018']
colors = ['#29378A', '#29378A', '#808080', '#808080']
markers = ['circle', 'square', 'circle', 'square']
names = ['Integrated - v24.10.0', 'Integrated - v24.11.0', 'Pure design - v24.10.0', 'Pure design - v24.11.0']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)

versions2test = ['v24.10.00', 'v24.11.00']
plot_version_mismatch()

Standard output:
  Page 1                                    Mon Mar 17 18:16:45 2025

  ******************************************************************
  *                           E P A N E T                          *
  *                   Hydraulic and Water Quality                  *
  *                   Analysis for Pipe Networks                   *
  *                         Version 2.3                            *
  ******************************************************************
  
Thanks for using BeMe-Sim!

Element with ID: 16723455349119256395 evaluated.
	Fitness vector: [6.6894e+06, -5.39165e-06]
	Elapsed time: 0 ms
Results saved in: /Users/zannads/repos/BevarMejo/visual/16723455349119256395.fv.json
EPANET project deleted

Standard error:

Return code:
0
Standard output:
  Page 1                                    Mon Mar 17 18:16:45 2025

  ******************************************************************
  *                           E P A N E T                 

Nothing changed, as I was expecting. 

## v24.12.0 aka inverted riser
Point: this should not be possible. A parameter should not hcange the mathematial solution. This hidners reproducibility. It doesn't invalide anything.
It would be interesting to quantify it for a generic network. 

Solution: A different heuristic to set the intial flows (it may even help with convergence).


In [9]:
# Same as before. We need to check v24.11.0 vs 24.12.0 for the mixed and rehab solutions
exps2plot = ['019', '025', '018', '024']
colors = ['#29378A', '#29378A', '#808080', '#808080']
markers = ['circle', 'square', 'circle', 'square']
names = ['Integrated - v24.10.0', 'Integrated - v24.12.0', 'Pure design - v24.10.0', 'Pure design - v24.12.0']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)

versions2test = ['v24.11.00', 'v24.12.00']
plot_version_mismatch()

Standard output:
  Page 1                                    Mon Mar 17 18:16:50 2025

  ******************************************************************
  *                           E P A N E T                          *
  *                   Hydraulic and Water Quality                  *
  *                   Analysis for Pipe Networks                   *
  *                         Version 2.3                            *
  ******************************************************************
  
Thanks for using BeMe-Sim!

Element with ID: 12159073217366282406 evaluated.
	Fitness vector: [6.64122e+06, -0.00152727]
	Elapsed time: 0 ms
Results saved in: /Users/zannads/repos/BevarMejo/visual/12159073217366282406.fv.json
EPANET project deleted

Standard error:

Return code:
0
Standard output:
  Page 1                                    Mon Mar 17 18:16:50 2025

  ******************************************************************
  *                           E P A N E T                 

## V25.02.00 aka New EPANET version (after bug)

Point: we need better issue tracking. This point hinders reproducibility. 

Solutio: add patch version to EPANET 2.3.1 etc 

In [10]:
# Same as before. We need to check v24.12.0 vs 25.02.0 for the mixed and rehab solutions
exps2plot = ['025', '031', '024', '030']
colors = ['#29378A', '#29378A', '#808080', '#808080']
markers = ['circle', 'square', 'circle', 'square']
names = ['Integrated - v24.12.0', 'Integrated - v25.02.0', 'Pure design - v24.12.0', 'Pure design - v25.02.0']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)

versions2test = ['v24.12.00', 'v25.02.00']
plot_version_mismatch()

Standard output:
  Page 1                                    Mon Mar 17 18:16:55 2025

  ******************************************************************
  *                           E P A N E T                          *
  *                   Hydraulic and Water Quality                  *
  *                   Analysis for Pipe Networks                   *
  *                         Version 2.3                            *
  ******************************************************************
  
Thanks for using BeMe-Sim!

Element with ID: 13169218993146467000 evaluated.
	Fitness vector: [6.56622e+06, -0.0022958]
	Elapsed time: 1 ms
Results saved in: /Users/zannads/repos/BevarMejo/visual/13169218993146467000.fv.json
EPANET project deleted

Standard error:
An error happend while executing a post-run task:
Task: Check correctness
function: check_correctness
  where: /Users/zannads/repos/BevarMejo/cli/src/simulator.cpp, 488
  what: Simulations results don't match the expected fitness v

## Formulation 2 vs Formulation 3 (new objective function)

Point: the results of EPANET should be a hard constraint to consider. Implemeting the failure as a "soft" constraint doesn't work.

1. fof1: failure is accounting putting reliability at 0 at that step.
2. fof2: failure is checked before everything and it is reuqired (hard constrained)

The prolem with the first one is that the EA, still manages to find solutions hat maybe are unfeasible for a little bit instead of going for fully feasible solutions that work worst.

In [11]:
# Same as before. We need to check v25.02.0 vs 25.03.0 for the mixed and rehab solutions
exps2plot = ['030', '032', '031', '033']
colors = ['#808080', '#808080', '#29378A', '#29378A']
markers = ['circle', 'square', 'circle', 'square']
names = ['Pure design :: f2', 'Pure design :: f3', 'Integrated :: f2', 'Integrated :: f3']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)

formulations2test = [2, 3]
plot_formulation_mismatch()

Standard output:
  Page 1                                    Mon Mar 17 18:17:01 2025

  ******************************************************************
  *                           E P A N E T                          *
  *                   Hydraulic and Water Quality                  *
  *                   Analysis for Pipe Networks                   *
  *                         Version 2.3                            *
  ******************************************************************
  
Thanks for using BeMe-Sim!

Element with ID: 11477768233698898354 evaluated.
	Fitness vector: [7.62564e+06, 1.7551]
	Elapsed time: 1 ms
Results saved in: /Users/zannads/repos/BevarMejo/visual/11477768233698898354.fv.json
EPANET project deleted

Standard error:
An error happend while executing a post-run task:
Task: Check correctness
function: check_correctness
  where: /Users/zannads/repos/BevarMejo/cli/src/simulator.cpp, 488
  what: Simulations results don't match the expected fitness vecto

In [12]:
# Same as before. We need to check v25.02.0 vs 25.03.0 for the mixed and rehab solutions
exps2plot = ['032', '034', '033', '035']
colors = ['#808080', '#808080', '#29378A', '#29378A']
markers = ['circle', 'square', 'circle', 'square']
names = ['Pure design :: f3', 'Pure design :: f4', 'Integrated :: f3', 'Integrated :: f4']
plot_pareto_fronts(experiments, exps2plot, colors, markers, names)

formulations2test = [2, 3]
plot_formulation_mismatch()

KeyError: '034'